In [ ]:
!pip install -U -q PyDrive 

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Mounted at /content/drive


In [ ]:
import os
import json
import argparse 

import numpy as np
import tensorflow as tf
from keras.models import Sequential, load_model
from keras.layers import LSTM, Dropout, TimeDistributed, Dense, Activation, Embedding

In [ ]:
data = []
text = ''
for i, (dirpath, dirnames, filenames) in enumerate(os.walk('/content/drive/MyDrive/FYP/Data/', topdown=False)):
    # print(i, dirpath, dirnames, filenames)
    for f in filenames: #f = name of file, not full file path 
        file_path = os.path.join(dirpath, f)
        print(file_path)
        file1 = open(file_path,"r")
        txt=file1.read()
        text = text + txt
        data.append(txt)

/content/drive/MyDrive/FYP/Data/jigs.txt
/content/drive/MyDrive/FYP/Data/morris.txt
/content/drive/MyDrive/FYP/Data/playford.txt
/content/drive/MyDrive/FYP/Data/reels A-C.txt
/content/drive/MyDrive/FYP/Data/reels D-G.txt
/content/drive/MyDrive/FYP/Data/reels H-L.txt
/content/drive/MyDrive/FYP/Data/reels M-Q.txt
/content/drive/MyDrive/FYP/Data/reels R-T.txt
/content/drive/MyDrive/FYP/Data/slip.txt
/content/drive/MyDrive/FYP/Data/waltez.txt
/content/drive/MyDrive/FYP/Data/input.txt
/content/drive/MyDrive/FYP/Data/hornpipes.txt
/content/drive/MyDrive/FYP/Data/ashover.txt
/content/drive/MyDrive/FYP/Data/reels u-z.txt


In [ ]:
text

'X: 1\nT:A and D\n% Nottingham Music Database\nS:EF\nM:4/4\nK:A\nM:6/8\nP:A\nf|"A"ecc c2f|"A"ecc c2f|"A"ecc c2f|"Bm"BcB "E7"B2f|\n"A"ecc c2f|"A"ecc c2c/2d/2|"D"efe "E7"dcB| [1"A"Ace a2:|\n [2"A"Ace ag=g||\\\nK:D\nP:B\n"D"f2f Fdd|"D"AFA f2e/2f/2|"G"g2g ecd|"Em"efd "A7"cBA|\n"D"f^ef dcd|"D"AFA f=ef|"G"gfg "A7"ABc |1"D"d3 d2e:|2"D"d3 d2||\n\n\n\nX: 2\nT:Abacus\n% Nottingham Music Database\nS:By Hugh Barwell, via Phil Rowe\nM:6/8\nK:G\n"G"g2g B^AB|d2d G3|"Em"GAB "Am"A2A|"D7"ABc "G"BAG|\n"G"g2g B^AB|d2d G2G|"Em"GAB "Am"A2G|"D7"FGA "G"G3::\n"D7"A^GA DFA|"G"B^AB G3|"A7"^c=c^c Ace|"D7"fef def|\n"G"g2g de=f|"E7"e2e Bcd|"Am"c2c "D7"Adc| [1"G"B2A G3:|\n [2"G"B2A G2F||"Em"E2E G2G|B2B e2e|"Am"c2A "B7"FBA|"Em"G2F E3|"Em"EFG "Am"ABc|\n"B7"B^c^d "Em"e2e|"F#7"f2f f2e|"B7"^def BAF|"Em"E2E G2G|B2B e2e|\n"Am"c2A "B7"FBA|"Em"G2F E3|"Em"EFG "Am"ABc|"B7"B^c^d "Em"e2e|\n"F#7"f2e "B7"^def |[1"Em"e3 "D7"d3:|[2"Em"e3 "E7"e3||\n\n\nX: 3\nT:The American Dwarf\n% Nottingham Music Database\nS:FTB, via EF\nM:6/8\nK:D

In [ ]:
BATCH_SIZE = 207
SEQ_LENGTH = 64

def read_batches(T, vocab_size):
    length = T.shape[0]; 
    batch_chars = int(length / BATCH_SIZE);

    for start in range(0, batch_chars - SEQ_LENGTH, SEQ_LENGTH):
        X = np.zeros((BATCH_SIZE, SEQ_LENGTH))
        Y = np.zeros((BATCH_SIZE, SEQ_LENGTH, vocab_size)) 
        for batch_idx in range(0, BATCH_SIZE): 
            for i in range(0, SEQ_LENGTH): 
                X[batch_idx, i] = T[batch_chars * batch_idx + start + i] # 
                Y[batch_idx, i, T[batch_chars * batch_idx + start + i + 1]] = 1
        yield X, Y

In [ ]:
def build_model(batch_size, seq_len, vocab_size, activation_function):
    model = Sequential()
    model.add(Embedding(vocab_size, 512, batch_input_shape=(batch_size, seq_len)))
    for i in range(4):
        model.add(LSTM(256, return_sequences=True, stateful=True))
        model.add(Dropout(0.2))

    model.add(TimeDistributed(Dense(vocab_size))) 
    model.add(Activation(activation_function))
    return model

In [ ]:
char_to_idx = { ch: i for (i, ch) in enumerate(sorted(list(set(text)))) }
print("Number of unique characters: " + str(len(char_to_idx))) #95
    
with open('/content/drive/MyDrive/FYP/char_to_idx.json', 'w') as f:
  json.dump(char_to_idx, f)

idx_to_char = { i: ch for (ch, i) in char_to_idx.items() }
vocab_size = len(char_to_idx)


Number of unique characters: 95


In [ ]:
epochs = 100

In [ ]:
model1= build_model(BATCH_SIZE, SEQ_LENGTH, vocab_size, 'softmax')
model1.summary()
opt = tf.keras.optimizers.Adam(learning_rate=0.1)
model1.compile(loss='categorical_crossentropy', optimizer=opt, metrics=['accuracy'])

T = np.asarray([char_to_idx[c] for c in text], dtype=np.int32) 

print("Length of text:" + str(T.size)) 

steps_per_epoch = (len(text) / BATCH_SIZE - 1) / SEQ_LENGTH  

loss_model1 = []
accuracy_model1 = []

for epoch in range(epochs):
  print('\nEpoch {}/{}'.format(epoch + 1, epochs))
  
  losses, accs = [], []

  for i, (X, Y) in enumerate(read_batches(T, vocab_size)):
    loss, acc = model1.train_on_batch(X, Y)
    print('Batch {}: loss = {}, acc = {}'.format(i + 1, loss, acc))
    losses.append(loss)
    accs.append(acc)
  loss_model1.append(losses)
  accuracy_model1.append(accs)

Streaming output truncated to the last 5000 lines.
Batch 52: loss = 3.720790147781372, acc = 0.1339070051908493
Batch 53: loss = 3.7624452114105225, acc = 0.12681159377098083
Batch 54: loss = 3.7765989303588867, acc = 0.12711352109909058
Batch 55: loss = 3.7769834995269775, acc = 0.12537741661071777
Batch 56: loss = 3.7868292331695557, acc = 0.12817029654979706
Batch 57: loss = 3.729282855987549, acc = 0.13013285398483276
Batch 58: loss = 3.7043442726135254, acc = 0.1332276612520218
Batch 59: loss = 3.682373046875, acc = 0.13662439584732056
Batch 60: loss = 3.7200875282287598, acc = 0.13209541141986847
Batch 61: loss = 3.765209913253784, acc = 0.13307669758796692
Batch 62: loss = 3.7863643169403076, acc = 0.12635870277881622
Batch 63: loss = 3.8086066246032715, acc = 0.12137681245803833
Batch 64: loss = 3.7225520610809326, acc = 0.12688708305358887
Batch 65: loss = 3.615511655807495, acc = 0.1451539844274521
Batch 66: loss = 3.761730432510376, acc = 0.13352958858013153
Batch 67: loss =

In [ ]:
print(loss_model1)
print(accuracy_model1)

[[4.553761005401611, 4.527628421783447, 9.378954887390137, 8.681408882141113, 9.838430404663086, 11.832306861877441, 13.500950813293457, 15.01180648803711, 13.980368614196777, 13.397479057312012, 13.367128372192383, 15.293553352355957, 14.458756446838379, 13.79207706451416, 14.597132682800293, 15.933443069458008, 16.648561477661133, 15.581392288208008, 15.960161209106445, 14.94737434387207, 13.187318801879883, 12.730560302734375, 13.030656814575195, 13.85918140411377, 13.350954055786133, 12.452555656433105, 12.448261260986328, 12.27053165435791, 12.090782165527344, 11.234182357788086, 11.616151809692383, 11.093087196350098, 10.18112564086914, 9.324129104614258, 9.016044616699219, 8.102136611938477, 7.789040565490723, 7.895930767059326, 7.676604270935059, 7.163689613342285, 7.174973487854004, 6.941203594207764, 7.210147380828857, 6.649739742279053, 6.547224521636963, 6.557993412017822, 6.532609939575195, 6.0605669021606445, 5.819675445556641, 5.604611396789551, 5.551847457885742, 5.4824

In [ ]:
model2= build_model(BATCH_SIZE, SEQ_LENGTH, vocab_size, 'softmax')
model2.summary()
opt = tf.keras.optimizers.SGD()
model2.compile(loss='categorical_crossentropy', optimizer=opt, metrics=['accuracy'])

T = np.asarray([char_to_idx[c] for c in text], dtype=np.int32) 

print("Length of text:" + str(T.size)) 

steps_per_epoch = (len(text) / BATCH_SIZE - 1) / SEQ_LENGTH  

loss_model2 = []
accuracy_model2 = []

for epoch in range(epochs):
  print('\nEpoch {}/{}'.format(epoch + 1, epochs))
  
  losses, accs = [], []

  for i, (X, Y) in enumerate(read_batches(T, vocab_size)):
    loss, acc = model2.train_on_batch(X, Y)
    print('Batch {}: loss = {}, acc = {}'.format(i + 1, loss, acc))
    losses.append(loss)
    accs.append(acc)
  loss_model2.append(losses)
  accuracy_model2.append(accs)

Streaming output truncated to the last 5000 lines.
Batch 52: loss = 3.3716540336608887, acc = 0.14024758338928223
Batch 53: loss = 3.398451089859009, acc = 0.1366998851299286
Batch 54: loss = 3.3885152339935303, acc = 0.13813406229019165
Batch 55: loss = 3.4047296047210693, acc = 0.13534118235111237
Batch 56: loss = 3.398559331893921, acc = 0.13919082283973694
Batch 57: loss = 3.3536877632141113, acc = 0.14243659377098083
Batch 58: loss = 3.330869197845459, acc = 0.1458333283662796
Batch 59: loss = 3.3063504695892334, acc = 0.15164552628993988
Batch 60: loss = 3.3417952060699463, acc = 0.14334239065647125
Batch 61: loss = 3.3937389850616455, acc = 0.1408514529466629
Batch 62: loss = 3.422785997390747, acc = 0.1339070051908493
Batch 63: loss = 3.4125404357910156, acc = 0.1349637657403946
Batch 64: loss = 3.331146717071533, acc = 0.13919082283973694
Batch 65: loss = 3.269789457321167, acc = 0.15828804671764374
Batch 66: loss = 3.3491251468658447, acc = 0.14658816158771515
Batch 67: loss 

In [ ]:
print(loss_model2)
print(accuracy_model2)

[[4.553952217102051, 4.55312967300415, 4.552186489105225, 4.550991058349609, 4.549949645996094, 4.549028396606445, 4.548302173614502, 4.547256946563721, 4.546010494232178, 4.544826030731201, 4.544174671173096, 4.543300628662109, 4.542379856109619, 4.541114330291748, 4.539794921875, 4.539247035980225, 4.538224220275879, 4.537315845489502, 4.535953521728516, 4.5349440574646, 4.534358501434326, 4.532721996307373, 4.532217025756836, 4.531137466430664, 4.529401779174805, 4.528378009796143, 4.52769660949707, 4.527883529663086, 4.525918006896973, 4.525400638580322, 4.524213790893555, 4.52419900894165, 4.522342205047607, 4.521027565002441, 4.52052116394043, 4.518214702606201, 4.518321514129639, 4.5173211097717285, 4.516071796417236, 4.515297889709473, 4.5140156745910645, 4.513531684875488, 4.513115882873535, 4.511610984802246, 4.510324954986572, 4.5090651512146, 4.508687496185303, 4.505797386169434, 4.505483150482178, 4.504269123077393, 4.504471302032471, 4.502614974975586, 4.503462314605713, 

In [ ]:
model3 = build_model(BATCH_SIZE, SEQ_LENGTH, vocab_size, 'softmax')
model3.summary()
opt = tf.keras.optimizers.SGD(learning_rate=0.1)
model3.compile(loss='categorical_crossentropy', optimizer=opt, metrics=['accuracy'])

T = np.asarray([char_to_idx[c] for c in text], dtype=np.int32) 

print("Length of text:" + str(T.size)) 

steps_per_epoch = (len(text) / BATCH_SIZE - 1) / SEQ_LENGTH  

loss_model3 = []
accuracy_model3 = []

for epoch in range(epochs):
  print('\nEpoch {}/{}'.format(epoch + 1, epochs))
  
  losses, accs = [], []

  for i, (X, Y) in enumerate(read_batches(T, vocab_size)):
    loss, acc = model3.train_on_batch(X, Y)
    print('Batch {}: loss = {}, acc = {}'.format(i + 1, loss, acc))
    losses.append(loss)
    accs.append(acc)
  loss_model3.append(losses)
  accuracy_model3.append(accs)

Streaming output truncated to the last 5000 lines.
Batch 52: loss = 2.059393882751465, acc = 0.4129680097103119
Batch 53: loss = 2.070652723312378, acc = 0.4090428650379181
Batch 54: loss = 2.0508546829223633, acc = 0.4160628020763397
Batch 55: loss = 2.0963916778564453, acc = 0.4030042290687561
Batch 56: loss = 2.07797908782959, acc = 0.4057970941066742
Batch 57: loss = 2.0793590545654297, acc = 0.4108544588088989
Batch 58: loss = 2.06733775138855, acc = 0.4027777910232544
Batch 59: loss = 2.0460124015808105, acc = 0.4088919162750244
Batch 60: loss = 2.0979201793670654, acc = 0.3999848961830139
Batch 61: loss = 2.1418042182922363, acc = 0.3912288546562195
Batch 62: loss = 2.142899990081787, acc = 0.3938707709312439
Batch 63: loss = 2.1212496757507324, acc = 0.39402174949645996
Batch 64: loss = 2.023486375808716, acc = 0.4083635210990906
Batch 65: loss = 2.090773582458496, acc = 0.39923006296157837
Batch 66: loss = 2.0944666862487793, acc = 0.40964674949645996
Batch 67: loss = 2.046494

In [ ]:
print(loss_model3)
print(accuracy_model3)

[[4.55403470993042, 4.543862819671631, 4.532191276550293, 4.519774436950684, 4.50840425491333, 4.496673583984375, 4.48856258392334, 4.47594690322876, 4.460727691650391, 4.444458484649658, 4.433836460113525, 4.418731689453125, 4.404648303985596, 4.38148832321167, 4.355343341827393, 4.337826728820801, 4.313251972198486, 4.284445762634277, 4.247167110443115, 4.209108352661133, 4.175848007202148, 4.127206802368164, 4.101271629333496, 4.068528652191162, 4.023291110992432, 4.000150203704834, 3.9903995990753174, 4.001969337463379, 3.954624891281128, 3.9464406967163086, 3.9325528144836426, 3.938824415206909, 3.901353597640991, 3.875491142272949, 3.8803951740264893, 3.8464765548706055, 3.8610575199127197, 3.8435511589050293, 3.824924945831299, 3.823031425476074, 3.818807601928711, 3.8235201835632324, 3.836073637008667, 3.81807279586792, 3.8019747734069824, 3.783566474914551, 3.790701389312744, 3.7796220779418945, 3.7753493785858154, 3.767416477203369, 3.7676241397857666, 3.767153739929199, 3.81

In [ ]:
import pandas as pd
import statistics


In [ ]:
softmax_lr = {}
loss_avg = []
loss_median = []
loss_std = []
loss_variance = []
loss_max = []
loss_min = []
for l in loss_model1:
  loss_avg.append(statistics.mean(l))
  loss_median.append(statistics.median(l))
  loss_std.append(statistics.stdev(l))
  loss_variance.append(statistics.variance(l))
  loss_max.append(max(l))
  loss_min.append(min(l))

softmax_lr['softmax_lr_avg'] = loss_avg
softmax_lr['softmax_lr_median'] = loss_median
softmax_lr['softmax_lr_std'] = loss_std
softmax_lr['softmax_lr_var'] = loss_variance
softmax_lr['softmax_lr_max'] = loss_max
softmax_lr['softmax_lr_min'] = loss_min



NameError: ignored

In [ ]:
softmax_lr.keys()

dict_keys(['softmax_lr_avg', 'softmax_lr_median', 'softmax_lr_std', 'softmax_lr_var', 'softmax_lr_max', 'softmax_lr_min'])

In [ ]:
sgd = {}
loss_avg = []
loss_median = []
loss_std = []
loss_variance = []
loss_max = []
loss_min = []
for l in loss_model2:
  loss_avg.append(statistics.mean(l))
  loss_median.append(statistics.median(l))
  loss_std.append(statistics.stdev(l))
  loss_variance.append(statistics.variance(l))
  loss_max.append(max(l))
  loss_min.append(min(l))

sgd['sgd_avg'] = loss_avg
sgd['sgd_median'] = loss_median
sgd['sgd_std'] = loss_std
sgd['sgd_var'] = loss_variance
sgd['sgd_max'] = loss_max
sgd['sgd_min'] = loss_min

In [ ]:
sgd.keys()

dict_keys(['sgd_avg', 'sgd_median', 'sgd_std', 'sgd_var', 'sgd_max', 'sgd_min'])

In [ ]:
sgd_lr = {}
loss_avg = []
loss_median = []
loss_std = []
loss_variance = []
loss_max = []
loss_min = []
for l in loss_model2:
  loss_avg.append(statistics.mean(l))
  loss_median.append(statistics.median(l))
  loss_std.append(statistics.stdev(l))
  loss_variance.append(statistics.variance(l))
  loss_max.append(max(l))
  loss_min.append(min(l))

sgd_lr['sgd_lr_avg'] = loss_avg
sgd_lr['sgd_lr_median'] = loss_median
sgd_lr['sgd_lr_std'] = loss_std
sgd_lr['sgd_lr_var'] = loss_variance
sgd_lr['sgd_lr_max'] = loss_max
sgd_lr['sgd_lr_min'] = loss_min

In [ ]:
pd1 = pd.DataFrame(softmax_lr, columns=softmax_lr.keys() )
pd1

softmax_lr_avg  softmax_lr_median  ...  softmax_lr_max  softmax_lr_min
0         6.068157           3.954897  ...       16.648561        3.661601
1         3.740315           3.738668  ...        3.822704        3.636486
2         3.858052           3.783308  ...        4.437930        3.630174
3         6.472639           4.506955  ...       22.541883        3.804685
4        15.625724          15.995646  ...       27.756580        4.345606
..             ...                ...  ...             ...             ...
95        3.726026           3.722061  ...        3.819080        3.628724
96        3.731209           3.729166  ...        3.808429        3.614458
97        3.730300           3.726440  ...        3.811589        3.615066
98        3.745274           3.743679  ...        3.831268        3.616335
99        3.737965           3.731809  ...        3.831223        3.618209

[100 rows x 6 columns]

In [ ]:
pd2 = pd.DataFrame(sgd, columns=sgd.keys() )
pd2

sgd_avg  sgd_median   sgd_std   sgd_var   sgd_max   sgd_min
0   4.463066    4.471724  0.060359  0.003643  4.553952  4.331206
1   4.074242    4.048314  0.142245  0.020234  4.346906  3.837519
2   3.823134    3.821478  0.038173  0.001457  3.935697  3.722643
3   3.767158    3.764797  0.026931  0.000725  3.844895  3.666700
4   3.747678    3.745836  0.025943  0.000673  3.815936  3.644643
..       ...         ...       ...       ...       ...       ...
95  3.269694    3.266704  0.032998  0.001089  3.527153  3.183605
96  3.266795    3.262864  0.033082  0.001094  3.530097  3.183247
97  3.264108    3.260716  0.033041  0.001092  3.529347  3.180913
98  3.261401    3.258802  0.033430  0.001118  3.533979  3.177617
99  3.259077    3.255818  0.033330  0.001111  3.531645  3.170972

[100 rows x 6 columns]

In [ ]:
pd3 = pd.DataFrame(sgd_lr, columns=sgd_lr.keys() )
pd3

sgd_lr_avg  sgd_lr_median  sgd_lr_std  sgd_lr_var  sgd_lr_max  sgd_lr_min
0     4.463066       4.471724    0.060359    0.003643    4.553952    4.331206
1     4.074242       4.048314    0.142245    0.020234    4.346906    3.837519
2     3.823134       3.821478    0.038173    0.001457    3.935697    3.722643
3     3.767158       3.764797    0.026931    0.000725    3.844895    3.666700
4     3.747678       3.745836    0.025943    0.000673    3.815936    3.644643
..         ...            ...         ...         ...         ...         ...
95    3.269694       3.266704    0.032998    0.001089    3.527153    3.183605
96    3.266795       3.262864    0.033082    0.001094    3.530097    3.183247
97    3.264108       3.260716    0.033041    0.001092    3.529347    3.180913
98    3.261401       3.258802    0.033430    0.001118    3.533979    3.177617
99    3.259077       3.255818    0.033330    0.001111    3.531645    3.170972

[100 rows x 6 columns]

In [ ]:

loss_exp1 = pd.concat([pd1, pd2, pd3],axis=1 )
loss_exp1

softmax_lr_avg  softmax_lr_median  ...  sgd_lr_max  sgd_lr_min
0         6.068157           3.954897  ...    4.553952    4.331206
1         3.740315           3.738668  ...    4.346906    3.837519
2         3.858052           3.783308  ...    3.935697    3.722643
3         6.472639           4.506955  ...    3.844895    3.666700
4        15.625724          15.995646  ...    3.815936    3.644643
..             ...                ...  ...         ...         ...
95        3.726026           3.722061  ...    3.527153    3.183605
96        3.731209           3.729166  ...    3.530097    3.183247
97        3.730300           3.726440  ...    3.529347    3.180913
98        3.745274           3.743679  ...    3.533979    3.177617
99        3.737965           3.731809  ...    3.531645    3.170972

[100 rows x 18 columns]

In [ ]:
!ls /content/drive/MyDrive/FYP/Evaluation/

In [ ]:
loss_exp1.to_csv(r'/content/drive/MyDrive/FYP/Evaluation/loss_exp1.csv', index = True, index_label='Epocs')

In [ ]:
softmax_lr = {}
loss_avg = []
loss_median = []
loss_std = []
loss_variance = []
loss_max = []
loss_min = []
for l in accuracy_model1:
  loss_avg.append(statistics.mean(l))
  loss_median.append(statistics.median(l))
  loss_std.append(statistics.stdev(l))
  loss_variance.append(statistics.variance(l))
  loss_max.append(max(l))
  loss_min.append(min(l))

softmax_lr['softmax_lr_avg'] = loss_avg
softmax_lr['softmax_lr_median'] = loss_median
softmax_lr['softmax_lr_std'] = loss_std
softmax_lr['softmax_lr_var'] = loss_variance
softmax_lr['softmax_lr_max'] = loss_max
softmax_lr['softmax_lr_min'] = loss_min


In [ ]:
sgd = {}
loss_avg = []
loss_median = []
loss_std = []
loss_variance = []
loss_max = []
loss_min = []
for l in accuracy_model2:
  loss_avg.append(statistics.mean(l))
  loss_median.append(statistics.median(l))
  loss_std.append(statistics.stdev(l))
  loss_variance.append(statistics.variance(l))
  loss_max.append(max(l))
  loss_min.append(min(l))

sgd['sgd_avg'] = loss_avg
sgd['sgd_median'] = loss_median
sgd['sgd_std'] = loss_std
sgd['sgd_var'] = loss_variance
sgd['sgd_max'] = loss_max
sgd['sgd_min'] = loss_min

In [ ]:
sgd_lr = {}
loss_avg = []
loss_median = []
loss_std = []
loss_variance = []
loss_max = []
loss_min = []
for l in accuracy_model3:
  loss_avg.append(statistics.mean(l))
  loss_median.append(statistics.median(l))
  loss_std.append(statistics.stdev(l))
  loss_variance.append(statistics.variance(l))
  loss_max.append(max(l))
  loss_min.append(min(l))

sgd_lr['sgd_lr_avg'] = loss_avg
sgd_lr['sgd_lr_median'] = loss_median
sgd_lr['sgd_lr_std'] = loss_std
sgd_lr['sgd_lr_var'] = loss_variance
sgd_lr['sgd_lr_max'] = loss_max
sgd_lr['sgd_lr_min'] = loss_min

In [ ]:
pd1 = pd.DataFrame(softmax_lr, columns=softmax_lr.keys() )
pd1

softmax_lr_avg  softmax_lr_median  ...  softmax_lr_max  softmax_lr_min
0         0.094065           0.108620  ...        0.139644        0.002189
1         0.130038           0.129680  ...        0.145154        0.120396
2         0.125857           0.129378  ...        0.145154        0.009662
3         0.096068           0.126887  ...        0.145229        0.005057
4         0.059186           0.038723  ...        0.139719        0.001812
..             ...                ...  ...             ...             ...
95        0.130038           0.129680  ...        0.145154        0.120396
96        0.130038           0.129680  ...        0.145154        0.120396
97        0.130038           0.129680  ...        0.145154        0.120396
98        0.130038           0.129680  ...        0.145154        0.120396
99        0.130038           0.129680  ...        0.145154        0.120396

[100 rows x 6 columns]

In [ ]:
pd2 = pd.DataFrame(sgd, columns=sgd.keys() )
pd2

sgd_avg  sgd_median   sgd_std   sgd_var   sgd_max   sgd_min
0   0.128144    0.129453  0.013763  0.000189  0.145154  0.008605
1   0.130038    0.129680  0.003916  0.000015  0.145154  0.120396
2   0.130028    0.129680  0.003913  0.000015  0.145229  0.120396
3   0.129989    0.129680  0.003922  0.000015  0.145305  0.120245
4   0.129928    0.129529  0.003917  0.000015  0.145154  0.120245
..       ...         ...       ...       ...       ...       ...
95  0.152350    0.152476  0.004674  0.000022  0.168780  0.136096
96  0.152910    0.152929  0.004565  0.000021  0.167497  0.135115
97  0.153098    0.153004  0.004875  0.000024  0.169988  0.138059
98  0.153153    0.153533  0.004852  0.000024  0.167648  0.132850
99  0.153566    0.153759  0.004820  0.000023  0.171573  0.134586

[100 rows x 6 columns]

In [ ]:
pd3 = pd.DataFrame(sgd_lr, columns=sgd_lr.keys() )
pd3

sgd_lr_avg  sgd_lr_median  sgd_lr_std  sgd_lr_var  sgd_lr_max  sgd_lr_min
0     0.129252       0.129604    0.010243    0.000105    0.145003    0.009888
1     0.129997       0.129604    0.003914    0.000015    0.145229    0.120320
2     0.130033       0.129680    0.003916    0.000015    0.145078    0.120320
3     0.129823       0.129529    0.003931    0.000015    0.145154    0.120396
4     0.130605       0.130586    0.004893    0.000024    0.148777    0.119188
..         ...            ...         ...         ...         ...         ...
95    0.497386       0.499094    0.016916    0.000286    0.521513    0.320501
96    0.498468       0.500528    0.016721    0.000280    0.527929    0.325257
97    0.501983       0.503321    0.016764    0.000281    0.525136    0.326162
98    0.503951       0.505661    0.016639    0.000277    0.527174    0.330616
99    0.503870       0.507171    0.018642    0.000348    0.527551    0.333786

[100 rows x 6 columns]

In [ ]:
accuracy_exp1 = pd.concat([pd1, pd2, pd3],axis=1 )
accuracy_exp1

softmax_lr_avg  softmax_lr_median  ...  sgd_lr_max  sgd_lr_min
0         0.094065           0.108620  ...    0.145003    0.009888
1         0.130038           0.129680  ...    0.145229    0.120320
2         0.125857           0.129378  ...    0.145078    0.120320
3         0.096068           0.126887  ...    0.145154    0.120396
4         0.059186           0.038723  ...    0.148777    0.119188
..             ...                ...  ...         ...         ...
95        0.130038           0.129680  ...    0.521513    0.320501
96        0.130038           0.129680  ...    0.527929    0.325257
97        0.130038           0.129680  ...    0.525136    0.326162
98        0.130038           0.129680  ...    0.527174    0.330616
99        0.130038           0.129680  ...    0.527551    0.333786

[100 rows x 18 columns]

In [ ]:
accuracy_exp1.to_csv(r'/content/drive/MyDrive/FYP/Evaluation/accuracy_exp1.csv', index = True, index_label='Epocs')